In [1]:
import pandas as pd
from os.path import join
from tqdm.notebook import tqdm
import json
import networkx as nx
from matplotlib.pyplot import figure
import numpy as np

REK_PATH = '/content/drive/MyDrive/PhD/Yousra_Data/Rekrute'
JO_OUT = 'data/transformed_data/job_offers_out'
JO_IN = 'data/source_data/job offers'
SKILL_OUT = 'data/transformed_data/extracted_skills'
ACC_DIR = 'data/transformed_data/acceptability'
COURSERA_PATH = 'data/source_data/courses'
KG_PATH = 'data/kg_data'

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [4]:
def write_json_lines(file_name,dict_data):
    json_string = json.dumps(dict_data)
    with open(file_name, 'a') as f:
        f.write(json_string+"\n")
        
def read_json_lines(file_name):
    lines = []
    with open(file_name) as file_in:
        for line in file_in:
            lines.append(json.loads(line))
    return lines
def inner_join_dfs(df_1, df_2, idx_1, idx_2):
    return df_1.set_index(idx_1).join(df_2.set_index(idx_2), how= 'inner').reset_index()

def add_skills_data():
    def filter_no_skills(str_list):
      return filter(None, str_list)
    df_jobs = pd.read_csv(join(JO_OUT, 'all_job_offers_clean.csv'))
    fr_extracted_skills = pd.DataFrame(read_json_lines(join(ACC_DIR, 'filtered_hard_skills_jobs.jsonl')))
    fr_extracted_skills = fr_extracted_skills.rename(columns={'acceptable_skills': 'fr_hard_skills', 'id': 'job_offer_id'})
    fr_extracted_skills['fr_hard_skills'] = fr_extracted_skills['fr_hard_skills'].apply(filter_no_skills)
    fr_extracted_skills['fr_hard_skills'] = fr_extracted_skills['fr_hard_skills'].str.join('|')
    # return fr_extracted_skills
    jz_extracted_skills = pd.DataFrame(read_json_lines(join(SKILL_OUT, 'jz_extracted_skills_v1.jsonl')))
    jz_extracted_skills = jz_extracted_skills.rename(columns={'skills': 'en_hard_skills'})
    jz_extracted_skills = inner_join_dfs(jz_extracted_skills, fr_extracted_skills, 'job_offer_id', 'job_offer_id')
    jz_extracted_skills = inner_join_dfs(jz_extracted_skills, df_jobs, 'job_offer_id', 'job_offer_id')
    # return jz_extracted_skills
    jz_extracted_skills['all_hard_skills'] = jz_extracted_skills['fr_hard_skills'] +'|'+jz_extracted_skills['en_hard_skills']
    jz_extracted_skills['all_hard_skills'] = jz_extracted_skills['all_hard_skills'].str.split('|').apply(filter_no_skills).str.join('|')
    return jz_extracted_skills

## Get Full Data
Remark: the hard skills have been extracted in the local machine not colab

In [5]:
df_jobs = pd.read_csv(join(JO_OUT, 'all_job_offers_clean.csv'))

/usr/local/lib/python3.8/dist-packages/IPython/core/interactiveshell.py:3326: DtypeWarning: Columns (17,18) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [6]:
df_jobs.iloc[0,:]

job_title                                           Chargés de Clientèle en Assistance Technique
city                                                                                  casablanca
function                                                               Call Centers (métiers de)
sector                                                               Informatique / Electronique
Expérience requise                                                                  De 1 à 3 ans
Région                                              10 poste(s) sur Casablanca et région - Maroc
Niveau d'étude et formation                                                               Bac +2
Type de contrat                                                                              CDI
Télétravail                                                                              no info
soft_skills                                                                                  NaN
Entreprise                    

In [7]:
# df_jobs['locations'].unique()

In [8]:
all_jobs = add_skills_data()

<ipython-input-8-fc46b8f4634a>:1: DtypeWarning: Columns (17,18) have mixed types.Specify dtype option on import or set low_memory=False.
  all_jobs = add_skills_data()


In [9]:
all_jobs

job_offer_id en_hard_skills  \
0                 0                  
1                 0                  
2              1016       commerce   
3              1016       commerce   
4              1020                  
...             ...            ...   
32815         33599                  
32816         33600                  
32817         33600                  
32818         33601                  
32819         33601                  

                                          fr_hard_skills  \
0      matérielles, logicielles|prendre en compte|env...   
1      architecture des systèmes|prendre en charge|ma...   
2                    normes comptables|gestion du stress   
3      contrôle de gestion|gestion du stress|normes c...   
4      gérer l'escalade des problèmes|connaissance de...   
...                                                  ...   
32815  outils pédagogiques|l’organisation|assurer le ...   
32816  réaliser les opérations d’usinage (affutage, t...   
32817  fixer|gérer le déplacement des outils|opératio...   
32818  envoyer des reportings réguliers|participer à ...   
32819  participer à des missions à caractère académiq...   

                                          job_title        city  \
0      Chargés de Clientèle en Assistance Technique  casablanca   
1      Chargés de Clientèle en Assistance Technique  casablanca   
2                                 Consultant Junior     tétouan   
3                                 Consultant Junior     tétouan   
4              Directeur Administratif et Financier  casablanca   
...                                             ...         ...   
32815                           Chef de Piste (H/F)  casablanca   
32816                        Assistante Pédagogique  casablanca   
32817                        Assistante Pédagogique  casablanca   
32818                        Technicien Laboratoire  casablanca   
32819                        Technicien Laboratoire  casablanca   

                                          function  \
0                        Call Centers (métiers de)   
1                        Call Centers (métiers de)   
2                                  Audit / Conseil   
3                                  Audit / Conseil   
4                       Responsable de Département   
...                                            ...   
32815          Logistique / Transport (métiers de)   
32816  Assistanat de Direction / Services Généraux   
32817  Assistanat de Direction / Services Généraux   
32818                        Médical / Paramédical   
32819                        Médical / Paramédical   

                                 sector Expérience requise  \
0           Informatique / Electronique       De 1 à 3 ans   
1           Informatique / Electronique       De 1 à 3 ans   
2                      Conseil / Etudes      Moins de 1 an   
3                      Conseil / Etudes      Moins de 1 an   
4      Gestion / Comptabilité / Finance      De 5 à 10 ans   
...                                 ...                ...   
32815       Automobile / Motos / Cycles      De 5 à 10 ans   
32816          Enseignement / Formation       De 1 à 3 ans   
32817          Enseignement / Formation       De 1 à 3 ans   
32818                 Pharmacie / Santé      Moins de 1 an   
32819                 Pharmacie / Santé      Moins de 1 an   

                                             Région  \
0      10 poste(s) sur Casablanca et région - Maroc   
1      10 poste(s) sur Casablanca et région - Maroc   
2           1 poste(s) sur Tanger et région - Maroc   
3           1 poste(s) sur Tanger et région - Maroc   
4       1 poste(s) sur Casablanca et région - Maroc   
...                                             ...   
32815   1 poste(s) sur Casablanca et région - Maroc   
32816   1 poste(s) sur Casablanca et région - Maroc   
32817   1 poste(s) sur Casablanca et région - Maroc   
32818   1 poste(s) sur Casablanca et région - Maroc   
32819   1 poste(s) sur Ca

In [10]:
all_jobs.to_csv(join(JO_OUT, 'all_job_offers_clean_hardskills.csv'), index = False)

In [11]:
all_jobs.shape

(32820, 31)

## More Cleaning: Function and Sector

In [12]:
all_jobs = pd.read_csv(join(JO_OUT, 'all_job_offers_clean_hardskills.csv'))

In [13]:
all_jobs.iloc[0,:]

job_offer_id                                                                                   0
en_hard_skills                                                                               NaN
fr_hard_skills                                 matérielles, logicielles|prendre en compte|env...
job_title                                           Chargés de Clientèle en Assistance Technique
city                                                                                  casablanca
function                                                               Call Centers (métiers de)
sector                                                               Informatique / Electronique
Expérience requise                                                                  De 1 à 3 ans
Région                                              10 poste(s) sur Casablanca et région - Maroc
Niveau d'étude et formation                                                               Bac +2
Type de contrat               

In [14]:
def clean_sector_func(all_df):
    all_df['sector'] = all_df['sector'].str.replace(r"\(.*\)","")
    all_df['sector'] = all_df['sector'].str.strip()
    all_df['function'] = all_df['function'].str.replace(r"\(.*\)","")
    all_df['function'] = all_df['function'].str.strip()
    return all_df

In [15]:
all_jobs = clean_sector_func(all_df = all_jobs)

<ipython-input-14-aec10d0d0464>:2: FutureWarning: The default value of regex will change from True to False in a future version.
  all_df['sector'] = all_df['sector'].str.replace(r"\(.*\)","")
<ipython-input-14-aec10d0d0464>:4: FutureWarning: The default value of regex will change from True to False in a future version.
  all_df['function'] = all_df['function'].str.replace(r"\(.*\)","")


In [16]:
all_jobs.head()

job_offer_id en_hard_skills  \
0             0            NaN   
1             0            NaN   
2          1016       commerce   
3          1016       commerce   
4          1020            NaN   

                                      fr_hard_skills  \
0  matérielles, logicielles|prendre en compte|env...   
1  architecture des systèmes|prendre en charge|ma...   
2                normes comptables|gestion du stress   
3  contrôle de gestion|gestion du stress|normes c...   
4  gérer l'escalade des problèmes|connaissance de...   

                                      job_title        city  \
0  Chargés de Clientèle en Assistance Technique  casablanca   
1  Chargés de Clientèle en Assistance Technique  casablanca   
2                             Consultant Junior     tétouan   
3                             Consultant Junior     tétouan   
4          Directeur Administratif et Financier  casablanca   

                     function                            sector  \
0                Call Centers       Informatique / Electronique   
1                Call Centers       Informatique / Electronique   
2             Audit / Conseil                  Conseil / Etudes   
3             Audit / Conseil                  Conseil / Etudes   
4  Responsable de Département  Gestion / Comptabilité / Finance   

  Expérience requise                                        Région  \
0       De 1 à 3 ans  10 poste(s) sur Casablanca et région - Maroc   
1       De 1 à 3 ans  10 poste(s) sur Casablanca et région - Maroc   
2      Moins de 1 an       1 poste(s) sur Tanger et région - Maroc   
3      Moins de 1 an       1 poste(s) sur Tanger et région - Maroc   
4      De 5 à 10 ans   1 poste(s) sur Casablanca et région - Maroc   

  Niveau d'étude et formation  ...    pub_date    exp_date pub_date_day  \
0                      Bac +2  ...  05/06/2017  05/08/2017            5   
1                      Bac +2  ...  05/06/2017  05/08/2017            5   
2                         NaN  ...  02/02/2006  02/02/2006            2   
3                         NaN  ...  02/02/2006  02/02/2006            2   
4                         NaN  ...  23/06/2006  23/07/2006           23   

  pub_date_month pub_date_year exp_date_day exp_date_month exp_date_year  \
0              6          2017            5              8          2017   
1              6          2017            5              8          2017   
2              2          2006            2              2          2006   
3              2          2006            2              2          2006   
4              6          2006           23              7          2006   

    locations                                    all_hard_skills  
0  casablanca  matérielles, logicielles|prendre en compte|env...  
1  casablanca  architecture des systèmes|prendre en charge|ma...  
2     tétouan       normes comptables|gestion du stress|commerce  
3     tétouan  contrôle de gestion|gestion du stress|normes c...  
4  casablanca  gérer l'escalade des problèmes|connaissance de...  

[5 rows x 31 columns]

In [17]:
all_jobs['sector'].unique()

array(['Informatique / Electronique', 'Conseil / Etudes',
       'Gestion / Comptabilité / Finance', 'Call Centers',
       'Autres services', 'Multimédia / Internet', 'Marketing',
       'Communication / Publicité / RP',
       'Méthodes / Process / Industrialisation',
       'Commercial / Vente / Export',
       'Assistanat de Direction / Services Généraux',
       'Administration des ventes / SAV', 'Responsable de Département',
       'Logistique / Transport', 'Gestion projet / Etudes / R&D',
       'Audit / Conseil', 'Télécoms / Réseaux',
       'Automobile / Motos / Cycles', 'Médical / Paramédical',
       'Avocat / Juriste / Fiscaliste', 'Journalisme / Traduction',
       'Audiovisuel', 'Urbanisme / architecture',
       'Caméraman / Monteur / Preneur de son',
       'Travaux / Chantiers / BTP', 'Hôtellerie / Restauration', 'Presse',
       'Banque / Finance', 'Telecom',
       'Production / Qualité / Sécurité / Maintenance', 'Informatique',
       "Centre d'appel", 'Transport / 

In [18]:
all_jobs['function'].unique()

array(['Call Centers', 'Audit / Conseil', 'Responsable de Département',
       'Commercial / Vente / Export',
       'Production / Qualité / Sécurité / Maintenance',
       'RH / Personnel / Formation', 'Gestion / Comptabilité / Finance',
       'Assistanat de Direction / Services Généraux',
       'Informatique / Electronique', 'Journalisme / Traduction',
       'Méthodes / Process / Industrialisation',
       'Communication / Publicité / RP', 'Gestion projet / Etudes / R&D',
       'Avocat / Juriste / Fiscaliste', 'Multimédia / Internet',
       'Marketing', 'Administration des ventes / SAV',
       'Caméraman / Monteur / Preneur de son',
       'Travaux / Chantiers / BTP', 'Assurance', 'Télécoms / Réseaux',
       'Achats / Supply Chain', 'Enseignement', 'Médical / Paramédical',
       'Urbanisme / architecture', 'Logistique / Transport',
       'Hôtellerie / Restauration', nan,
       'Coursier / Gardiennage / Propreté', 'Agriculture',
       'Immobilier / Promotion', 'Banque', 'Im

In [19]:
all_jobs.to_csv(join(JO_OUT, 'all_job_offers_clean_hardskills_v2.csv'), index = False)

## Entities Extraction

In [20]:
def save_json(save_file, data):
    with open(save_file, 'w') as f:
        json.dump(data, f)
def decompress_str(str_, sep='|'):
    return [i.strip() for i in str_.split(sep)]
def decompress_str_list(sep='|'):
    def decompress_str_list_(st_list):
        return sum([decompress_str(st, sep) for st in st_list], [])
    return decompress_str_list_
    
def get_entity(df_, entity_type, entity_id_col , entity_attr_cols, process_ent=None):
    all_entities = []
    uni_ents = list(df_[entity_id_col].dropna().unique())
    print(type(uni_ents))
    if process_ent is not None:
        uni_ents = process_ent(uni_ents)
        if isinstance(uni_ents, list):
            uni_ents = list(set(uni_ents))
    print(type(uni_ents))
    for ent_id, ent_name in enumerate(tqdm(uni_ents)):
        data = {}
        if ent_name:
            data['ent_id'] = ent_id
            data['ent_attr'] = list(set(df_[df_[entity_id_col]==ent_id][entity_attr_cols].to_dict('records')))
            data['ent_name'] = ent_name
            all_entities.append(data)
        # if len(all_entities)>50:
        #    break
    return pd.DataFrame(all_entities)

In [21]:
df_jobs = pd.read_csv(join(JO_OUT, 'all_job_offers_clean_hardskills_v2.csv'))

In [22]:
df_jobs.iloc[0,:]

job_offer_id                                                                                   0
en_hard_skills                                                                               NaN
fr_hard_skills                                 matérielles, logicielles|prendre en compte|env...
job_title                                           Chargés de Clientèle en Assistance Technique
city                                                                                  casablanca
function                                                                            Call Centers
sector                                                               Informatique / Electronique
Expérience requise                                                                  De 1 à 3 ans
Région                                              10 poste(s) sur Casablanca et région - Maroc
Niveau d'étude et formation                                                               Bac +2
Type de contrat               

In [23]:
df_jobs

job_offer_id en_hard_skills  \
0                 0            NaN   
1                 0            NaN   
2              1016       commerce   
3              1016       commerce   
4              1020            NaN   
...             ...            ...   
32815         33599            NaN   
32816         33600            NaN   
32817         33600            NaN   
32818         33601            NaN   
32819         33601            NaN   

                                          fr_hard_skills  \
0      matérielles, logicielles|prendre en compte|env...   
1      architecture des systèmes|prendre en charge|ma...   
2                    normes comptables|gestion du stress   
3      contrôle de gestion|gestion du stress|normes c...   
4      gérer l'escalade des problèmes|connaissance de...   
...                                                  ...   
32815  outils pédagogiques|l’organisation|assurer le ...   
32816  réaliser les opérations d’usinage (affutage, t...   
32817  fixer|gérer le déplacement des outils|opératio...   
32818  envoyer des reportings réguliers|participer à ...   
32819  participer à des missions à caractère académiq...   

                                          job_title        city  \
0      Chargés de Clientèle en Assistance Technique  casablanca   
1      Chargés de Clientèle en Assistance Technique  casablanca   
2                                 Consultant Junior     tétouan   
3                                 Consultant Junior     tétouan   
4              Directeur Administratif et Financier  casablanca   
...                                             ...         ...   
32815                           Chef de Piste (H/F)  casablanca   
32816                        Assistante Pédagogique  casablanca   
32817                        Assistante Pédagogique  casablanca   
32818                        Technicien Laboratoire  casablanca   
32819                        Technicien Laboratoire  casablanca   

                                          function  \
0                                     Call Centers   
1                                     Call Centers   
2                                  Audit / Conseil   
3                                  Audit / Conseil   
4                       Responsable de Département   
...                                            ...   
32815                       Logistique / Transport   
32816  Assistanat de Direction / Services Généraux   
32817  Assistanat de Direction / Services Généraux   
32818                        Médical / Paramédical   
32819                        Médical / Paramédical   

                                 sector Expérience requise  \
0           Informatique / Electronique       De 1 à 3 ans   
1           Informatique / Electronique       De 1 à 3 ans   
2                      Conseil / Etudes      Moins de 1 an   
3                      Conseil / Etudes      Moins de 1 an   
4      Gestion / Comptabilité / Finance      De 5 à 10 ans   
...                                 ...                ...   
32815       Automobile / Motos / Cycles      De 5 à 10 ans   
32816          Enseignement / Formation       De 1 à 3 ans   
32817          Enseignement / Formation       De 1 à 3 ans   
32818                 Pharmacie / Santé      Moins de 1 an   
32819                 Pharmacie / Santé      Moins de 1 an   

                                             Région  \
0      10 poste(s) sur Casablanca et région - Maroc   
1      10 poste(s) sur Casablanca et région - Maroc   
2           1 poste(s) sur Tanger et région - Maroc   
3           1 poste(s) sur Tanger et région - Maroc   
4       1 poste(s) sur Casablanca et région - Maroc   
...                                             ...   
32815   1 poste(s) sur Casablanca et région - Maroc   
32816   1 poste(s) sur Casablanca et région - Maroc   
32817   1 poste(s) sur Casablanca et région - Maroc   
32818   1 poste(s) sur Casablanca et région - Maroc   
32819   1 poste(s) sur Ca

In [24]:
df_jobs['locations'].unique()

array(['casablanca', 'tétouan', 'marrakech', 'rabat',
       'casablanca|marrakech|agadir', 'casablanca|rabat', 'bouskoura',
       'agadir', 'marrakech|agadir', 'casablanca|marrakech',
       'rabat|marrakech', 'kenitra', 'casablanca|rabat|marrakech',
       'mohammedia', 'temara', 'casablanca|rabat|fès|marrakech',
       'casablanca|agadir', 'fès', 'meknès', 'el jadid',
       'casablanca|fès|marrakech', 'fès|agadir',
       'casablanca|rabat|mohammedia', 'tangier', 'nador',
       'casablanca|rabat|marrakech|agadir', 'fès|marrakech|meknès',
       'casablanca|rabat|marrakech|meknès', 'rabat|safi|el jadid',
       'casablanca|rabat|safi|el jadid', 'settat', 'marrakech|settat',
       'casablanca|bouskoura', 'casablanca|meknès', 'béni mellal',
       'fès|meknès|agadir', 'casablanca|rabat|el jadid',
       'rabat|fès|agadir', 'rabat|fès|marrakech', 'fès|meknès|tétouan',
       'casablanca|fès', 'casablanca|meknès|agadir', 'tiflet',
       'sidi slimane', 'casablanca|rabat|fès',
      

### Extract jobs titles

In [25]:
dta = get_entity(df_=df_jobs, entity_type ='job_title',entity_id_col='job_title' , entity_attr_cols = [], process_ent=None)

<class 'list'>
<class 'list'>


  0%|          | 0/9736 [00:00<?, ?it/s]

In [26]:
dta.head()

ent_id ent_attr                                      ent_name
0       0       []  Chargés de Clientèle en Assistance Technique
1       1       []                             Consultant Junior
2       2       []          Directeur Administratif et Financier
3       3       []                  Sales Managers Hispanophones
4       4       []                   Sales Managers Francophones

In [27]:
dta.shape

(9736, 3)

In [28]:
dta.to_csv(join(KG_PATH, 'entities', 'job_titles.csv'), index = False)

### Extract Soft Skills

In [29]:
dta = get_entity(df_=df_jobs, entity_type ='soft_skills',entity_id_col='soft_skills' , entity_attr_cols = [], process_ent=decompress_str_list('|'))

<class 'list'>
<class 'list'>


  0%|          | 0/21 [00:00<?, ?it/s]

In [30]:
dta.head()

ent_id ent_attr                 ent_name
0       0       []  Intuition / Spontanéité
1       1       []            Improvisation
2       2       []    Volonté de persuasion
3       3       []                 Humilité
4       4       []   Recherche de nouveauté

In [31]:
dta.to_csv(join(KG_PATH, 'entities', 'soft_skills.csv'), index = False)

### Extract Hard Skills

In [32]:
dta = get_entity(df_=df_jobs, entity_type ='all_hard_skills',entity_id_col='all_hard_skills' , entity_attr_cols = [], process_ent=decompress_str_list('|'))

<class 'list'>
<class 'list'>


  0%|          | 0/31010 [00:00<?, ?it/s]

In [33]:
dta.head()

ent_id ent_attr                                  ent_name
0       0       []                   etablir un plan à moyen
1       1       []  harmoniser les compétences par formation
2       2       []           gérer le déplacement des outils
3       3       []      prendre connaissance de l'ordonnance
4       4       []                           donner un feed-

In [34]:
dta

ent_id ent_attr                                           ent_name
0           0       []                            etablir un plan à moyen
1           1       []           harmoniser les compétences par formation
2           2       []                    gérer le déplacement des outils
3           3       []               prendre connaissance de l'ordonnance
4           4       []                                    donner un feed-
...       ...      ...                                                ...
31005   31005       []          garantir la traçabilité des interventions
31006   31006       []                 installer le matériel informatique
31007   31007       []                        prendre contact avec le drh
31008   31008       []  assurer les relations extérieures avec les exp...
31009   31009       []  réaliser des tableaux de bord et des rapports ...

[31010 rows x 3 columns]

In [35]:
dta.to_csv(join(KG_PATH, 'entities', 'hard_skills.csv'), index = False)

### Companies

In [36]:
recruiter_df = pd.DataFrame(read_json_lines(join(JO_IN, 'recruiter.jsonl')))

In [37]:
recruiter_df = recruiter_df.rename(columns = {'recruiter_id':'ent_id', 'company':'ent_name'})

In [38]:
recruiter_df.to_csv(join(KG_PATH, 'entities', 'recruiters.csv'), index = False)

### Sectors

In [39]:
# df_jobs['sector'].unique()

In [40]:
dta = get_entity(df_=df_jobs, entity_type ='sector',entity_id_col='sector' , entity_attr_cols = [], process_ent=decompress_str_list('/'))

<class 'list'>
<class 'list'>


  0%|          | 0/133 [00:00<?, ?it/s]

In [41]:
dta.head()

ent_id ent_attr           ent_name
0       0       []  Services Généraux
1       1       []       Evénementiel
2       2       []         Parfumerie
3       3       []          Peintures
4       4       []     Centre d'appel

In [42]:
dta.to_csv(join(KG_PATH, 'entities', 'sector.csv'), index = False)

### Functions
city 	function

In [43]:
dta = get_entity(df_=df_jobs, entity_type ='function',entity_id_col='function' , entity_attr_cols = [], process_ent=decompress_str_list('/'))

<class 'list'>
<class 'list'>


  0%|          | 0/75 [00:00<?, ?it/s]

In [44]:
dta

ent_id ent_attr                    ent_name
0        0       []           Services Généraux
1        1       []                   Transport
2        2       []                      Export
3        3       []               Communication
4        4       []              Gestion projet
..     ...      ...                         ...
70      70       []                Call Centers
71      71       []                  Production
72      72       []  Responsable de Département
73      73       []                    Méthodes
74      74       []                     Réseaux

[75 rows x 3 columns]

In [45]:
dta.to_csv(join(KG_PATH, 'entities', 'function.csv'), index = False)

### Cities

In [46]:
df_jobs['locations'].unique()

array(['casablanca', 'tétouan', 'marrakech', 'rabat',
       'casablanca|marrakech|agadir', 'casablanca|rabat', 'bouskoura',
       'agadir', 'marrakech|agadir', 'casablanca|marrakech',
       'rabat|marrakech', 'kenitra', 'casablanca|rabat|marrakech',
       'mohammedia', 'temara', 'casablanca|rabat|fès|marrakech',
       'casablanca|agadir', 'fès', 'meknès', 'el jadid',
       'casablanca|fès|marrakech', 'fès|agadir',
       'casablanca|rabat|mohammedia', 'tangier', 'nador',
       'casablanca|rabat|marrakech|agadir', 'fès|marrakech|meknès',
       'casablanca|rabat|marrakech|meknès', 'rabat|safi|el jadid',
       'casablanca|rabat|safi|el jadid', 'settat', 'marrakech|settat',
       'casablanca|bouskoura', 'casablanca|meknès', 'béni mellal',
       'fès|meknès|agadir', 'casablanca|rabat|el jadid',
       'rabat|fès|agadir', 'rabat|fès|marrakech', 'fès|meknès|tétouan',
       'casablanca|fès', 'casablanca|meknès|agadir', 'tiflet',
       'sidi slimane', 'casablanca|rabat|fès',
      

In [47]:
df_jobs['locations'].unique()

array(['casablanca', 'tétouan', 'marrakech', 'rabat',
       'casablanca|marrakech|agadir', 'casablanca|rabat', 'bouskoura',
       'agadir', 'marrakech|agadir', 'casablanca|marrakech',
       'rabat|marrakech', 'kenitra', 'casablanca|rabat|marrakech',
       'mohammedia', 'temara', 'casablanca|rabat|fès|marrakech',
       'casablanca|agadir', 'fès', 'meknès', 'el jadid',
       'casablanca|fès|marrakech', 'fès|agadir',
       'casablanca|rabat|mohammedia', 'tangier', 'nador',
       'casablanca|rabat|marrakech|agadir', 'fès|marrakech|meknès',
       'casablanca|rabat|marrakech|meknès', 'rabat|safi|el jadid',
       'casablanca|rabat|safi|el jadid', 'settat', 'marrakech|settat',
       'casablanca|bouskoura', 'casablanca|meknès', 'béni mellal',
       'fès|meknès|agadir', 'casablanca|rabat|el jadid',
       'rabat|fès|agadir', 'rabat|fès|marrakech', 'fès|meknès|tétouan',
       'casablanca|fès', 'casablanca|meknès|agadir', 'tiflet',
       'sidi slimane', 'casablanca|rabat|fès',
      

In [48]:
dta = get_entity(df_=df_jobs, entity_type ='locations',entity_id_col='locations' , entity_attr_cols = [], process_ent=decompress_str_list('|'))

<class 'list'>
<class 'list'>


  0%|          | 0/35 [00:00<?, ?it/s]

In [49]:
dta.head()

ent_id ent_attr    ent_name
0       0       []  benslimane
1       1       []  errachidia
2       2       []         fès
3       3       []  casablanca
4       4       []      tiflet

In [50]:
dta

ent_id ent_attr      ent_name
0        0       []    benslimane
1        1       []    errachidia
2        2       []           fès
3        3       []    casablanca
4        4       []        tiflet
5        5       []      ouezzane
6        6       []          safi
7        7       []          sale
8        8       []        temara
9        9       []      taounate
10      10       []        sefrou
11      11       []        meknès
12      12       []     essaouira
13      13       []  sidi slimane
14      14       []      oued zem
15      15       []         nador
16      16       []       tangier
17      17       []     marrakech
18      18       []      skhirate
19      19       []       larache
20      20       []      khénifra
21      21       []  ain el aouda
22      22       []      taourirt
23      23       []   ait melloul
24      24       []    mohammedia
25      25       []       kenitra
26      26       []    youssoufia
27      27       []      el jadid
28      28       []        agadir
29      29       []        settat
30      30       []     bouskoura
31      31       []   béni mellal
32      32       []          taza
33      33       []       tétouan
34      34       []         rabat

In [51]:
dta.to_csv(join(KG_PATH, 'entities', 'locations.csv'), index = False)

### Courses

In [52]:
coursera_data = pd.DataFrame(read_json_lines(join(COURSERA_PATH, 'coursera_courses.jsonl')))

In [53]:
coursera_data = coursera_data.rename(columns = {'id':'ent_id', 'name':'ent_name'})

In [54]:
coursera_data.to_csv(join(KG_PATH, 'entities', 'coursera.csv'), index = False)

In [55]:
pd.read_csv(join(KG_PATH, 'entities', 'coursera.csv'))

courseType                                        description  \
0      v2.ondemand  In this two-hour, project-based course, we int...   
1      v2.ondemand  À la fin de ce projet, vous aurez toutes les c...   
2      v2.ondemand  ينشئ العديد من الأشخاص حسابات وسائط اجتماعية م...   
3      v2.ondemand  Gamification is the application of game elemen...   
4      v2.ondemand  This course will cover the steps used in weigh...   
...            ...                                                ...   
10175  v2.ondemand  This course will provide a detailed  overview ...   
10176  v2.ondemand  This course introduces Korean characters,'Hang...   
10177  v2.ondemand  This is a Google Cloud Self-Paced Lab. In this...   
10178  v2.ondemand  In this 3-hour long project-based course, you ...   
10179  v2.ondemand  This course offers a rigorous mathematical sur...   

                       ent_id  \
0      NJSdGN71Eeq4CApSN3OTvQ   
1      DMkcgX7LEeyRTg6FtAvfBw   
2      YLO0oGSUEeyIUg4Qv2RsBQ   
3      69Bku0KoEeWZtA4u62x6lQ   
4      0HiU7Oe4EeWTAQ4yevf_oQ   
...                       ...   
10175  QJlWBW30Eeq2hwr9iuARBQ   
10176  XSLeWQ6pEeu9ZBLzQTJEhw   
10177  7ErrkakwEeyxDg4ukgkVlw   
10178  xcqAU7oaEeq1DQ4cuiU-Sw   
10179  tJApe-HgEeeSKxKWkG_JMg   

                                                    slug instructorIds  \
0      make-pick-ups-look-cool-unity-introduction-ani...   ['4730641']   
1              integrer-applications-dashboard-hootsuite  ['26958800']   
2                      getting-started-with-hootsuite-ar  ['76377122']   
3                                           gamification    ['226710']   
4                                           missing-data   ['8394050']   
...                                                  ...           ...   
10175                                 strategic-sourcing  ['48414296']   
10176     the-korean-alphabet-an-introduction-to-hangeul  ['73075287']   
10177   googlecloud-looker-functions-and-operators-j9rv9  ['22997770']   
10178    build-a-film-club-web-app-with-google-appengine    ['154346']   
10179                                   causal-inference  ['36507528']   

      specializations partnerIds  \
0                  []    ['565']   
1                  []    ['565']   
2                  []    ['565']   
3                  []      ['6']   
4                  []     ['32']   
...               ...        ...   
10175              []     ['67']   
10176              []    ['668']   
10177              []    ['443']   
10178              []    ['565']   
10179              []     ['40']   

                                                ent_name  page  
0      Make Your Pick-Ups Look Cool in Unity (Intro t...     0  
1      Intégrer des applications dans votre Dashboard...     0  
2                         كيفية استعمال التطبيق هووتسويت     0  
3                                           Gamification     0  
4                              Dealing With Missing Data     0  
...                                                  ...   ...  
10175                                 Strategic Sourcing     4  
10176    The Korean Alphabet: An Introduction to Hangeul     4  
10177                     Looker Functions and Operators     4  
10178      Build a film club web app on Google AppEngine     4  
10179                                   Causal Inference     4  

[10180 rows x 9 columns]

### Courses Skills Addition

In [56]:
def add_skills_data_coursera():
    def filter_no_skills(str_list):
        return filter(None, str_list)
    coursera_data = pd.DataFrame(read_json_lines(join(COURSERA_PATH, 'coursera_courses.jsonl')))
    # fr_skills = pd.DataFrame(read_json_lines(join(COURSERA_PATH, 'fr_coursera_extracted_skills_v2.jsonl')))
    fr_skills = pd.DataFrame(read_json_lines(join(ACC_DIR, 'filtered_hard_skills_coursera.jsonl')))
    fr_skills = fr_skills.rename(columns={'acceptable_skills': 'fr_hard_skills'})
    fr_skills['fr_hard_skills'] = fr_skills['fr_hard_skills'].apply(filter_no_skills)
    fr_skills['fr_hard_skills'] = fr_skills['fr_hard_skills'].str.join('|')
    # return fr_skills
    en_skills = pd.DataFrame(read_json_lines(join(COURSERA_PATH, 'jz_coursera_extracted_skills_v1.jsonl')))
    en_skills = en_skills.rename(columns={'skills': 'en_hard_skills'})
    coursera_data = inner_join_dfs(coursera_data, fr_skills, 'id', 'id')
    coursera_data = inner_join_dfs(coursera_data, en_skills, 'id', 'id')
    coursera_data['all_hard_skills'] = coursera_data['fr_hard_skills'] +'|'+coursera_data['en_hard_skills'] 
    coursera_data['all_hard_skills'] = coursera_data['all_hard_skills'].str.split('|').apply(filter_no_skills).str.join('|')
    return coursera_data

In [57]:
coursera_data = add_skills_data_coursera()

In [58]:
# coursera_data.to_csv(join(join(COURSERA_PATH, 'coursera_courses_hard_skills.csv')), index = False)

In [59]:
coursera_data

id   courseType  \
0     --626KkxEeywagovoAKHOQ  v2.ondemand   
1     --626KkxEeywagovoAKHOQ  v2.ondemand   
2     -0wI4W8lEeys9RJMWW48Yw  v2.ondemand   
3     -0wI4W8lEeys9RJMWW48Yw  v2.ondemand   
4     -3PuGcl0Eeuiewq9VRQV-Q  v2.ondemand   
...                      ...          ...   
2537  zpu5n6ksEeyxDg4ukgkVlw  v2.ondemand   
2538  zvWn57E8EeiktBIa9lPubg  v2.ondemand   
2539  zvWn57E8EeiktBIa9lPubg  v2.ondemand   
2540  zxPc1BgjEeyf4Ar-aygVCw  v2.ondemand   
2541  zxPc1BgjEeyf4Ar-aygVCw  v2.ondemand   

                                            description  \
0     This is a self-paced lab that takes place in t...   
1     This is a self-paced lab that takes place in t...   
2     Ce projet vous permet de créer des visuels var...   
3     Ce projet vous permet de créer des visuels var...   
4     Welcome to this project-based course, Working ...   
...                                                 ...   
2537  This is a self-paced lab that takes place in t...   
2538  Actualmente la probabilidad se ha convertido e...   
2539  Actualmente la probabilidad se ha convertido e...   
2540  Dans ce cours d'une heure, basé sur un projet,...   
2541  Dans ce cours d'une heure, basé sur un projet,...   

                                                   slug  \
0     googlecloud-provisioning-an-apigee-x-evaluatio...   
1     googlecloud-provisioning-an-apigee-x-evaluatio...   
2          creer-visuels-facebook-picmonkey-entreprises   
3          creer-visuels-facebook-picmonkey-entreprises   
4                        working-with-subqueries-in-sql   
...                                                 ...   
2537         googlecloud-apis-explorer-app-engine-2gpn6   
2538                                       probabilidad   
2539                                       probabilidad   
2540              traefik-ingress-controller-kubernetes   
2541              traefik-ingress-controller-kubernetes   

                       instructorIds specializations partnerIds  \
0                         [22997770]              []      [443]   
1                         [22997770]              []      [443]   
2                         [26958800]              []      [565]   
3                         [26958800]              []      [565]   
4                         [40353561]              []      [565]   
...                              ...             ...        ...   
2537                      [22997770]              []      [443]   
2538  [35721552, 35717185, 39954673]              []      [273]   
2539  [35721552, 35717185, 39954673]              []      [273]   
2540                      [52260949]              []      [565]   
2541                      [52260949]              []      [565]   

                                                   name  page  \
0      Provisioning an Apigee X Evaluation Organization     2   
1      Provisioning an Apigee X Evaluation Organization     2   
2     Créer des visuels Facebook avec PicMonkey pour...     3   
3     Créer des visuels Facebook avec PicMonkey pour...     3   
4                        Working with Subqueries in SQL     4   
...                                                 ...   ...   
2537                          APIs Explorer: App Engine     4   
2538         Fundamentos de probabilidad y aplicaciones     3   
2539         Fundamentos de probabilidad y aplicaciones     3   
2540  Créer un ingress controller dans Kubernetes av...     1   
2541  Créer un ingress controller dans Kubernetes av...     1   

                                         fr_hard_skills  \
0                                                         
1                                              business   
2     améliorer la visibilité de votre marque en lig...   
3     compétences de base|créer des visuels variés|c...   
4                                            postgresql   
...                                                 ...   
2537                                   outil de gestion   
2538     

In [60]:
dta = get_entity(df_=coursera_data, entity_type ='all_hard_skills',entity_id_col='all_hard_skills' , entity_attr_cols = [], process_ent=decompress_str_list(sep='|'))

<class 'list'>
<class 'list'>


  0%|          | 0/2251 [00:00<?, ?it/s]

In [61]:
# these hard skills need to be added to the existing hard skills
dta

ent_id ent_attr                             ent_name
0          1       []   analyser les réponses automatiques
1          2       []                suivre les actualités
2          3       []                     cloud monitoring
3          4       []   identifier les exigences du projet
4          5       []  mesurer la satisfaction des clients
...      ...      ...                                  ...
2245    2246       []                créer un loadbalancer
2246    2247       []      bases de données relationnelles
2247    2248       []         étudier différentes manières
2248    2249       []                           durability
2249    2250       []                              g suite

[2250 rows x 3 columns]

In [62]:
hard_skills = pd.read_csv(join(KG_PATH,'entities', 'hard_skills.csv'))

In [63]:
hard_skills

ent_id ent_attr                                           ent_name
0           0       []                            etablir un plan à moyen
1           1       []           harmoniser les compétences par formation
2           2       []                    gérer le déplacement des outils
3           3       []               prendre connaissance de l'ordonnance
4           4       []                                    donner un feed-
...       ...      ...                                                ...
31005   31005       []          garantir la traçabilité des interventions
31006   31006       []                 installer le matériel informatique
31007   31007       []                        prendre contact avec le drh
31008   31008       []  assurer les relations extérieures avec les exp...
31009   31009       []  réaliser des tableaux de bord et des rapports ...

[31010 rows x 3 columns]

In [64]:
dta['ent_id'] = dta['ent_id'] + hard_skills['ent_id'].max()

In [65]:
dta

ent_id ent_attr                             ent_name
0      31010       []   analyser les réponses automatiques
1      31011       []                suivre les actualités
2      31012       []                     cloud monitoring
3      31013       []   identifier les exigences du projet
4      31014       []  mesurer la satisfaction des clients
...      ...      ...                                  ...
2245   33255       []                créer un loadbalancer
2246   33256       []      bases de données relationnelles
2247   33257       []         étudier différentes manières
2248   33258       []                           durability
2249   33259       []                              g suite

[2250 rows x 3 columns]

In [66]:
pd.concat([dta, hard_skills], ignore_index=True).shape

(33260, 3)

In [67]:
all_hard_skills = pd.concat([dta, hard_skills], ignore_index=True).drop_duplicates(subset= ['ent_name'])


In [68]:
all_hard_skills.to_csv(join(KG_PATH, 'entities', 'hard_skills.csv'), index = False)

## Triples Extraction

In [69]:
def exact_sim(key, data):
  if key in data:
      return data[key]
  else:
      return None
  
def in_sim(key, data):
    for k in data:
        if key in k:
            return data[k]
    return None
def str_in_sim(sep='|', strip=False):
    def str_in_sim_(key, data):
        if not isinstance(key, str):
            return None
        for k in data:
            if k in key.split(sep):
                if strip:
                    return data[k.strip()]
                else:
                    return data[k]
        return None
    return str_in_sim_

In [70]:
entities = ['hard_skills', 'coursera', 'job_titles', 'recruiters', 'soft_skills', 'locations', 'function', 'sector']
# schema = [
#     {'triple':('job_titles', 'recruiters', 'belongs_to'),'cols': ('job_title', 'recruiter_id', None),
#      'source' : 'rek_offers', 'sim_fun':(exact_sim, exact_sim, None)},
#     {'triple':('recruiters', 'job_titles', 'needs'),'cols': ('recruiter_id', 'job_title', None),
#      'source' : 'rek_offers', 'sim_fun':(exact_sim, exact_sim, None)},
#     {'triple':('job_titles', 'sector', 'has'),'cols': ('job_title', 'sector', None),
#      'source' : 'rek_offers', 'sim_fun':(exact_sim, str_in_sim(sep='/', strip=True), None)},
#     {'triple':('function', 'sector', 'co_occurs_with'),'cols': ('function', 'sector', None),
#      'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='/', strip=True), str_in_sim(sep='/', strip=True), None)},
#     {'triple':('hard_skills', 'coursera', 'aquired_by'),'cols': ('all_hard_skills', 'name', None),
#      'sim_fun':(str_in_sim(sep='|'), exact_sim, None), 'source' : 'coursera'},
#     {'triple':('coursera', 'hard_skills', 'provides'),'cols': ('name', 'all_hard_skills', None),
#      'source' : 'coursera', 'sim_fun':(exact_sim, str_in_sim(sep='|'), None)},
#     {'triple':('job_titles', 'soft_skills', 'requires'),'cols': ('job_title', 'soft_skills', None),
#      'source' : 'rek_offers', 'sim_fun':(exact_sim, str_in_sim(sep='|'), None)},
#     {'triple':('job_titles', 'hard_skills', 'requires'),'cols': ('job_title', 'all_hard_skills', None),
#      'source' : 'rek_offers', 'sim_fun':(exact_sim, str_in_sim(sep='|'), None)},
#     {'triple':('hard_skills', 'job_titles', 'needed_for'),'cols': ('all_hard_skills', 'job_title', None),
#      'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='|'), exact_sim, None)},
#     {'triple':('soft_skills', 'job_titles', 'needed_for'),'cols': ('soft_skills', 'job_title', None),
#      'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='|'), exact_sim, None)},
#     {'triple':('hard_skills', 'hard_skills', 'co_occurs_with'),'cols': ('all_hard_skills', 'all_hard_skills', None),
#      'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='|'), str_in_sim(sep='|'), None)},
#     {'triple':('hard_skills', 'soft_skills', 'co_occurs_with'),'cols': ('all_hard_skills', 'soft_skills', None),
#      'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='|'), str_in_sim(sep='|'), None)},
#     {'triple':('job_titles', 'locations', 'co_occurs_with'),'cols': ('job_title', 'locations', None),
#      'source' : 'rek_offers', 'sim_fun':(exact_sim, str_in_sim(sep='|'), None)},
#     {'triple':('job_titles', 'function', 'has'),'cols': ('job_title', 'function', None),
#      'source' : 'rek_offers', 'sim_fun':(exact_sim, str_in_sim(sep='/', strip=True), None)},
#     {'triple':('job_titles', 'locations', 'located'),'cols': ('job_title', 'locations', None),
#     'source' : 'rek_offers', 'sim_fun':(exact_sim, str_in_sim(sep='|'), None)}
# ]

schema = [
    {'triple':('job_titles', 'recruiters', 'belongs_to'),'cols': ('job_title', 'recruiter_id', None), #rec_job title
     'source' : 'rek_offers', 'sim_fun':(exact_sim, exact_sim, None)},
    {'triple':('recruiters', 'job_titles', 'needs'),'cols': ('recruiter_id', 'job_title', None),  # asymetric 
     'source' : 'rek_offers', 'sim_fun':(exact_sim, exact_sim, None)}, 
    {'triple':('sector', 'job_titles', 'has'),'cols': ('sector', 'job_title', None),       #sec_job title
     'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='/', strip=True), exact_sim, None)}, 
    {'triple':('job_titles', 'sector', 'belongs_to'),'cols': ('job_title', 'sector', None),    #asymetric
     'source' : 'rek_offers', 'sim_fun':(exact_sim, str_in_sim(sep='/', strip=True), None)},
    {'triple':('function', 'sector', 'co_occurs_with'),'cols': ('function', 'sector', None), #func_sector
     'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='/', strip=True), str_in_sim(sep='/', strip=True), None)},
    {'triple':('sector', 'function', 'co_occurs_with'),'cols': ('sector', 'function', None), #asymetric
     'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='/', strip=True), str_in_sim(sep='/', strip=True), None)},
    {'triple':('hard_skills', 'coursera', 'acquired_by'),'cols': ('all_hard_skills', 'name', None), #hs_coursera
     'sim_fun':(str_in_sim(sep='|'), exact_sim, None), 'source' : 'coursera'},
    {'triple':('coursera', 'hard_skills', 'provides'),'cols': ('name', 'all_hard_skills', None), #asymetric
     'source' : 'coursera', 'sim_fun':(exact_sim, str_in_sim(sep='|'), None)},      
    {'triple':('job_titles', 'soft_skills', 'requires'),'cols': ('job_title', 'soft_skills', None),      #jobs_ss
     'source' : 'rek_offers', 'sim_fun':(exact_sim, str_in_sim(sep='|'), None)},
    {'triple':('job_titles', 'hard_skills', 'requires'),'cols': ('job_title', 'all_hard_skills', None),  #jobs_hs
     'source' : 'rek_offers', 'sim_fun':(exact_sim, str_in_sim(sep='|'), None)},
    {'triple':('hard_skills', 'job_titles', 'needed_for'),'cols': ('all_hard_skills', 'job_title', None),  #asymetric_hs
     'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='|'), exact_sim, None)},
    {'triple':('soft_skills', 'job_titles', 'needed_for'),'cols': ('soft_skills', 'job_title', None),    #asymetric_ss
     'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='|'), exact_sim, None)},
    {'triple':('hard_skills', 'hard_skills', 'co_occurs_with'),'cols': ('all_hard_skills', 'all_hard_skills', None), #hs_hs
     'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='|'), str_in_sim(sep='|'), None)},
     {'triple':('soft_skills', 'soft_skills', 'co_occurs_with'),'cols': ('soft_skills', 'soft_skills', None), #ss_ss
     'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='|'), str_in_sim(sep='|'), None)},
    {'triple':('hard_skills', 'soft_skills', 'co_occurs_with'),'cols': ('all_hard_skills', 'soft_skills', None),  #hs_ss
     'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='|'), str_in_sim(sep='|'), None)},
    {'triple':('soft_skills', 'hard_skills', 'co_occurs_with'),'cols': ('soft_skills', 'all_hard_skills', None), #asymetric
     'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='|'), str_in_sim(sep='|'), None)},
    {'triple':('job_titles', 'function', 'has'),'cols': ('job_title', 'function', None), #jt_fun
     'source' : 'rek_offers', 'sim_fun':(exact_sim, str_in_sim(sep='/', strip=True), None)},
    {'triple':('function', 'job_titles', 'by'),'cols': ('function', 'job_title', None),  #asymetric
     'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='/', strip=True), exact_sim, None)},
    {'triple':('job_titles', 'locations', 'is_located'),'cols': ('job_title', 'locations', None), #jt_locs
    'source' : 'rek_offers', 'sim_fun':(exact_sim, str_in_sim(sep='|'), None)},
    {'triple':('locations', 'job_titles', 'locates'),'cols': ('locations', 'job_title',None),   #asymetric
    'source' : 'rek_offers', 'sim_fun':(str_in_sim(sep='|'), exact_sim, None)}
]


In [71]:
def get_entity_dicts():
    all_dict = {}
    hard_skills = pd.read_csv(join(KG_PATH, 'entities', 'hard_skills.csv'))
    all_dict['hard_skills'] = {k:v for k , v in zip(hard_skills['ent_name'], hard_skills['ent_id'])}
    coursera = pd.read_csv(join(KG_PATH, 'entities', 'coursera.csv'))
    all_dict['coursera'] = {k:v for k , v in zip(coursera['ent_name'], coursera['ent_id'])}
    job_titles = pd.read_csv(join(KG_PATH, 'entities', 'job_titles.csv'))
    all_dict['job_titles'] = {k:v for k , v in zip(job_titles['ent_name'], job_titles['ent_id'])}
    recruiters = pd.read_csv(join(KG_PATH, 'entities', 'recruiters.csv'))
    # all_dict['recruiters'] = {k:v for k , v in zip(recruiters['ent_name'], recruiters['ent_id'])}
    all_dict['recruiters'] = {k:v for k , v in zip(recruiters['ent_id'], recruiters['ent_id'])}
    soft_skills = pd.read_csv(join(KG_PATH, 'entities', 'soft_skills.csv')).dropna()
    all_dict['soft_skills'] = {k:v for k , v in zip(soft_skills['ent_name'], soft_skills['ent_id'])}
    function = pd.read_csv(join(KG_PATH, 'entities', 'function.csv'))
    all_dict['function'] = {k:v for k , v in zip(function['ent_name'], function['ent_id'])}
    locations = pd.read_csv(join(KG_PATH, 'entities', 'locations.csv'))
    all_dict['locations'] = {k:v for k , v in zip(locations['ent_name'], locations['ent_id'])}
    sector = pd.read_csv(join(KG_PATH, 'entities', 'sector.csv'))
    all_dict['sector'] = {k:v for k , v in zip(sector['ent_name'], sector['ent_id'])}
    return all_dict

def get_source_data():
    jo_df = pd.read_csv(join(JO_OUT, 'all_job_offers_clean_hardskills_v2.csv'))
    coursera_df = pd.read_csv(join(COURSERA_PATH, 'coursera_courses_hard_skills.csv'))
    # this is needed because some recruiters are not known
    jo_df['recruiter_id'] = pd.to_numeric(jo_df['recruiter_id'], errors='coerce')
    return {'rek_offers':jo_df, 'coursera':coursera_df}

def get_triples(
    trip_data, head_pre, tail_pre, rel_pre,
    ent_data_head, ent_data_tail, ent_data_rel,
    ent_col_head, ent_col_tail, ent_col_rel, c_head_func, c_tail_func, c_rel_func, add_time = True, col_time = 'pub_date'):
    all_triples = []
    pbar = tqdm(total = trip_data.shape[0])
    for i, rec in trip_data.iterrows():
        id_head = c_head_func(rec[ent_col_head], ent_data_head)
        id_tail = c_tail_func(rec[ent_col_tail], ent_data_tail)
        if col_time not in rec:
            rec[col_time] = '01/01/2005'
        if add_time:
            time_val = rec[col_time]
        if isinstance(ent_data_rel, dict):
            id_rel = c_rel_func(rec[ent_col_rel], ent_data_rel)
        elif isinstance(ent_data_rel, str):
            id_rel = ent_data_rel
        if None not in [id_head, id_tail, id_rel, time_val]:
            triple = {}
            triple['head'] = head_pre+'_'+ str(id_head)
            triple['tail'] = tail_pre +'_'+ str(id_tail)
            triple['rel'] = rel_pre +'_'+ str(id_rel)
            triple['time'] = time_val
            all_triples.append(triple)
        pbar.update()
    return all_triples

def get_all_triples():
    triples = []
    entity_dicts = get_entity_dicts()
    source_data = get_source_data()
    for s_el in tqdm(schema):
        s_triple =  s_el['triple']
        print(s_triple)
        s_sim_fun = s_el['sim_fun']
        s_cols = s_el['cols']
        s_source = s_el['source']
        triples += get_triples(
          trip_data= source_data[s_source], head_pre=s_triple[0], tail_pre = s_triple[1], rel_pre = '',
          ent_data_head = entity_dicts[s_triple[0]], ent_data_tail=entity_dicts[s_triple[1]], ent_data_rel = s_triple[2],
          ent_col_head = s_cols[0], ent_col_tail = s_cols[1], ent_col_rel = None,
          c_head_func=s_sim_fun[0], c_tail_func=s_sim_fun[1], c_rel_func = None)
    return triples

def chech_triples(triples_df):
    entity_counts = {}
    entity_triple_counts = {}
    for entity in tqdm(entities):
        head = list(triples_df[triples_df['head'].str.startswith(entity)]['head'])
        tail = list(triples_df[triples_df['tail'].str.startswith(entity)]['tail'])
        entity_triple_counts[entity] = len(head)+len(tail)
        entity_counts[entity] = len(list(set(head + tail)))
    return entity_counts, entity_triple_counts

def get_entity_contrib(df_):
    # head_ = df_['head'].value_counts().to_dict()
    head_ = df_.groupby(['head'])['count_col_sum'].agg('sum').to_dict()
    # return head_
    # tail_ = df_['tail'].value_counts().to_dict()
    tail_ = df_.groupby(['tail'])['count_col_sum'].agg('sum').to_dict()
    return {k: tail_.get(k, 0) + tail_.get(k, 0) for k in set(head_) | set(tail_)}
    
def get_entity_sccores_triples(df_):
    ent_rep = get_entity_contrib(df_)
    df_['head_c'] = df_['head'].map(ent_rep)
    df_['tail_c'] = df_['tail'].map(ent_rep)
    df_['total_c'] =  df_['head_c'] + df_['tail_c']
    df_['total_c'] = df_['count_col_sum']/df_['total_c']
    return df_
  
def get_good_triples(triples):
    triples['count_col'] = 1
    triples['time'] = pd.to_datetime(triples['time'])
    grouped = triples.groupby(['head','tail','rel']).agg({'count_col' : np.sum, 'time' : [np.min, np.max]})
    grouped.columns = grouped.columns.map('_'.join).str.strip('_')
    grouped = grouped.reset_index()
    triples_ = get_entity_sccores_triples(df_ = grouped)
    return triples_


In [72]:
triples = get_all_triples()

  0%|          | 0/20 [00:00<?, ?it/s]

('job_titles', 'recruiters', 'belongs_to')


  0%|          | 0/32820 [00:00<?, ?it/s]

('recruiters', 'job_titles', 'needs')


  0%|          | 0/32820 [00:00<?, ?it/s]

...

  0%|          | 0/32820 [00:00<?, ?it/s]

('job_titles', 'locations', 'is_located')


  0%|          | 0/32820 [00:00<?, ?it/s]

('locations', 'job_titles', 'locates')


  0%|          | 0/32820 [00:00<?, ?it/s]

In [73]:
triples = pd.DataFrame(triples)

In [74]:
triples.head()

head               tail          rel        time
0  job_titles_0  recruiters_127912  _belongs_to  05/06/2017
1  job_titles_0  recruiters_127912  _belongs_to  05/06/2017
2  job_titles_2    recruiters_1012  _belongs_to  23/06/2006
3  job_titles_2    recruiters_1012  _belongs_to  23/06/2006
4  job_titles_3    recruiters_1012  _belongs_to  12/02/2006

In [75]:
triples.to_csv(join(KG_PATH,'triples', 'raw_triples.csv'), index = False)

In [76]:
triples_ = get_good_triples(triples)

In [77]:
triples_['total_c'].max()

0.25

In [78]:
triples_.to_csv(join(KG_PATH,'triples', 'kg_triples.csv'), index = False)

## Check stats

In [148]:
triples_df = pd.DataFrame(triples).drop_duplicates(['head','tail','rel'])

In [149]:
entity_counts, entity_triple_counts = chech_triples(triples_df)

  0%|          | 0/8 [00:00<?, ?it/s]

In [150]:
entity_counts

{'hard_skills': 2174,
 'coursera': 7342,
 'job_titles': 9736,
 'recruiters': 1353,
 'soft_skills': 9,
 'locations': 34,
 'function': 11,
 'sector': 26}

In [151]:
entity_triple_counts

{'hard_skills': 50918,
 'coursera': 14708,
 'job_titles': 103756,
 'recruiters': 22622,
 'soft_skills': 26706,
 'locations': 21486,
 'function': 3330,
 'sector': 9500}

In [152]:
# triples_df.to_csv(join(KG_PATH, 'triples', 'triples_v1.csv'), index = False)

In [153]:
triples_df.shape

(126513, 5)

In [154]:
triples_df[triples_df['head'].str.startswith('job_titles')]

head               tail          rel       time  count_col
0          job_titles_0  recruiters_127912  _belongs_to 2017-05-06          1
1          job_titles_2    recruiters_1012  _belongs_to 2006-06-23          1
2          job_titles_3    recruiters_1012  _belongs_to 2006-12-02          1
3          job_titles_4    recruiters_1012  _belongs_to 2006-12-02          1
4          job_titles_5    recruiters_1012  _belongs_to 2006-06-23          1
...                 ...                ...          ...        ...        ...
211714  job_titles_9731        locations_8  _is_located 2013-09-07          1
211715  job_titles_9732        locations_8  _is_located 2013-10-07          1
211717  job_titles_9733        locations_8  _is_located 2013-10-07          1
211720  job_titles_9734        locations_8  _is_located 2013-10-07          1
211722  job_titles_9735        locations_8  _is_located 2013-11-07          1

[51878 rows x 5 columns]

In [155]:
pd.DataFrame(triples)

head               tail          rel       time  count_col
0       job_titles_0  recruiters_127912  _belongs_to 2017-05-06          1
1       job_titles_2    recruiters_1012  _belongs_to 2006-06-23          1
2       job_titles_3    recruiters_1012  _belongs_to 2006-12-02          1
3       job_titles_4    recruiters_1012  _belongs_to 2006-12-02          1
4       job_titles_5    recruiters_1012  _belongs_to 2006-06-23          1
...              ...                ...          ...        ...        ...
228131   locations_8     job_titles_164     _locates 2013-10-07          1
228132   locations_8    job_titles_9735     _locates 2013-11-07          1
228133   locations_8    job_titles_8742     _locates 2013-11-07          1
228134   locations_8    job_titles_9622     _locates 2013-12-07          1
228135   locations_8    job_titles_1825     _locates 2013-12-07          1

[228136 rows x 5 columns]

## Tests

In [ ]:
pd.DataFrame(triples)['head']+pd.DataFrame(triples)

In [ ]:
hard_skills_dict, coursera_dict, job_titles_dict, recruiters_dict, soft_skills_dict = get_entity_dicts()

In [ ]:
jo_df = pd.read_csv(join(JO_OUT, 'all_job_offers_clean_hardskills.csv'))
coursera_df = pd.read_csv(join(COURSERA_PATH, 'coursera_courses_hard_skills.csv'))

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:3326: DtypeWarning: Columns (19,20) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [ ]:
jo_df.iloc[0,:]

job_offer_id                                                                                   0
en_hard_skills                                                                               NaN
fr_hard_skills                                 préparer|s’|traiter les demandes|gérer des dem...
job_title                                           Chargés de Clientèle en Assistance Technique
city                                                                                  casablanca
function                                                               Call Centers (métiers de)
sector                                                               Informatique / Electronique
Expérience requise                                                                  De 1 à 3 ans
Région                                              10 poste(s) sur Casablanca et région - Maroc
Niveau d'étude et formation                                                               Bac +2
Type de contrat               

In [ ]:
jo_df['function'].unique()

array(['Call Centers (métiers de)', 'Audit / Conseil',
       'Responsable de Département', 'Commercial / Vente / Export',
       'Production / Qualité / Sécurité / Maintenance',
       'RH / Personnel / Formation', 'Gestion / Comptabilité / Finance',
       'Assistanat de Direction / Services Généraux',
       'Informatique / Electronique', 'Journalisme / Traduction',
       'Méthodes / Process / Industrialisation',
       'Communication / Publicité / RP', 'Gestion projet / Etudes / R&D',
       'Avocat / Juriste / Fiscaliste', 'Multimédia / Internet',
       'Marketing', 'Administration des ventes / SAV',
       'Caméraman / Monteur / Preneur de son',
       'Travaux / Chantiers / BTP', "Assurance (métiers de l')",
       'Télécoms / Réseaux', 'Achats / Supply Chain', 'Enseignement',
       'Médical / Paramédical', 'Urbanisme / architecture',
       'Logistique / Transport (métiers de)',
       'Hôtellerie / Restauration (métiers de)', nan,
       'Coursier / Gardiennage / Propreté',

In [ ]:
jo_df['sector'].unique()

array(['Informatique / Electronique', 'Conseil / Etudes',
       'Gestion / Comptabilité / Finance', 'Call Centers (métiers de)',
       'Autres services', 'Multimédia / Internet', 'Marketing',
       'Communication / Publicité / RP',
       'Méthodes / Process / Industrialisation',
       'Commercial / Vente / Export',
       'Assistanat de Direction / Services Généraux',
       'Administration des ventes / SAV', 'Responsable de Département',
       'Logistique / Transport (métiers de)',
       'Gestion projet / Etudes / R&D', 'Audit / Conseil',
       'Télécoms / Réseaux', 'Automobile / Motos / Cycles',
       'Médical / Paramédical', 'Avocat / Juriste / Fiscaliste',
       'Journalisme / Traduction', 'Audiovisuel',
       'Urbanisme / architecture', 'Caméraman / Monteur / Preneur de son',
       'Travaux / Chantiers / BTP', 'Hôtellerie / Restauration', 'Presse',
       'Banque / Finance', 'Telecom',
       'Production / Qualité / Sécurité / Maintenance', 'Informatique',
       "Cent

In [ ]:
jo_df.head()

job_offer_id en_hard_skills  \
0             0            NaN   
1          1016       commerce   
2          1020            NaN   
3          1021       business   
4          1022       business   

                                      fr_hard_skills  \
0  préparer|s’|traiter les demandes|gérer des dem...   
1                                                NaN   
2   connaissance des normes|audit|aspects financiers   
3  résolution des problèmes|mener|coacher|recrute...   
4  résolution des problèmes|mener|coacher|recrute...   

                                      job_title        city  \
0  Chargés de Clientèle en Assistance Technique  casablanca   
1                             Consultant Junior     tétouan   
2          Directeur Administratif et Financier  casablanca   
3                  Sales Managers Hispanophones  casablanca   
4                   Sales Managers Francophones  casablanca   

                      function                            sector  \
0    Call Centers (métiers de)       Informatique / Electronique   
1              Audit / Conseil                  Conseil / Etudes   
2   Responsable de Département  Gestion / Comptabilité / Finance   
3  Commercial / Vente / Export         Call Centers (métiers de)   
4   Responsable de Département         Call Centers (métiers de)   

  Expérience requise                                        Région  \
0       De 1 à 3 ans  10 poste(s) sur Casablanca et région - Maroc   
1      Moins de 1 an       1 poste(s) sur Tanger et région - Maroc   
2      De 5 à 10 ans   1 poste(s) sur Casablanca et région - Maroc   
3      De 5 à 10 ans   5 poste(s) sur Casablanca et région - Maroc   
4      De 5 à 10 ans   5 poste(s) sur Casablanca et région - Maroc   

  Niveau d'étude et formation  ...    pub_date    exp_date pub_date_day  \
0                      Bac +2  ...  05/06/2017  05/08/2017            5   
1                         NaN  ...  02/02/2006  02/02/2006            2   
2                         NaN  ...  23/06/2006  23/07/2006           23   
3                         NaN  ...  12/02/2006  16/03/2006           12   
4                         NaN  ...  12/02/2006  16/03/2006           12   

  pub_date_month pub_date_year exp_date_day exp_date_month exp_date_year  \
0              6          2017            5              8          2017   
1              2          2006            2              2          2006   
2              6          2006           23              7          2006   
3              2          2006           16              3          2006   
4              2          2006           16              3          2006   

    locations                                    all_hard_skills  
0  casablanca  préparer|s’|traiter les demandes|gérer des dem...  
1     tétouan                                          |commerce  
2  casablanca  connaissance des normes|audit|aspects financiers|  
3  casablanca  résolution des problèmes|mener|coacher|recrute...  
4  casablanca  résolution des problèmes|mener|coacher|recrute...  

[5 rows x 31 columns]

In [ ]:
coursera_df.head()

id   courseType  \
0  NJSdGN71Eeq4CApSN3OTvQ  v2.ondemand   
1  DMkcgX7LEeyRTg6FtAvfBw  v2.ondemand   
2  YLO0oGSUEeyIUg4Qv2RsBQ  v2.ondemand   
3  69Bku0KoEeWZtA4u62x6lQ  v2.ondemand   
4  0HiU7Oe4EeWTAQ4yevf_oQ  v2.ondemand   

                                         description  \
0  In this two-hour, project-based course, we int...   
1  À la fin de ce projet, vous aurez toutes les c...   
2  ينشئ العديد من الأشخاص حسابات وسائط اجتماعية م...   
3  Gamification is the application of game elemen...   
4  This course will cover the steps used in weigh...   

                                                slug instructorIds  \
0  make-pick-ups-look-cool-unity-introduction-ani...   ['4730641']   
1          integrer-applications-dashboard-hootsuite  ['26958800']   
2                  getting-started-with-hootsuite-ar  ['76377122']   
3                                       gamification    ['226710']   
4                                       missing-data   ['8394050']   

  specializations partnerIds  \
0              []    ['565']   
1              []    ['565']   
2              []    ['565']   
3              []      ['6']   
4              []     ['32']   

                                                name  page  \
0  Make Your Pick-Ups Look Cool in Unity (Intro t...     0   
1  Intégrer des applications dans votre Dashboard...     0   
2                     كيفية استعمال التطبيق هووتسويت     0   
3                                       Gamification     0   
4                          Dealing With Missing Data     0   

                                      fr_hard_skills  \
0                                                 c#   
1  intégrer|installer|découvrir|compétences de ba...   
2                                                NaN   
3                                                NaN   
4                                                NaN   

              en_hard_skills  \
0                      unity   
1                    tableau   
2                        NaN   
3  design|business|languages   
4      missing data|software   

                                     all_hard_skills  
0                                           c#|unity  
1  intégrer|installer|découvrir|compétences de ba...  
2                                                  |  
3                         |design|business|languages  
4                             |missing data|software

In [ ]:
coursera_dict

{'Make Your Pick-Ups Look Cool in Unity (Intro to Animation 1)': 'NJSdGN71Eeq4CApSN3OTvQ',
 'Intégrer des applications dans votre Dashboard Hootsuite': 'DMkcgX7LEeyRTg6FtAvfBw',
 'كيفية استعمال التطبيق هووتسويت': 'YLO0oGSUEeyIUg4Qv2RsBQ',
 'Gamification': '69Bku0KoEeWZtA4u62x6lQ',
 'Dealing With Missing Data': '0HiU7Oe4EeWTAQ4yevf_oQ',
 'Unordered Data Structures': 'sI_-QEBiEemtDRLx7Ne8jg',
 "Installation et configuration du pack d'extension C-C++ avec Visual Studio Code": '2WtDgaCrEeyFDhLpwtOZqw',
 'Migrating to Cloud SQL from Amazon RDS for MySQL Using Database Migration Service': 'rrZX06kxEeyjPxJkzIUqCw',
 'Vital Signs: Understanding What the Body Is Telling Us': '5zjIsJq-EeW_wArffOXkOw',
 'FinTech Disruptive Innovation: Implications for Society': 'WFanvtoSEeedbRLwgi9a7A',
 ' Cluster Analysis using RCmdr': 'zjIfbv3pEeqRMRJTGi3b6Q',
 'Analyze Network Traffic with TCPDump': 'k-WxP98PEeypqArgW5gGjw',
 'Modern Art & Ideas': 'v9CQdBkhEeWjrA6seF25aw',
 'The Evolving Universe': 'QgmoVdT2Ee

In [ ]:
triples = get_triples(
    trip_data= coursera_df, head_pre='coursera', tail_pre = 'hard_skills', rel_pre = '',
    ent_data_head = coursera_dict, ent_data_tail=hard_skills_dict, ent_data_rel = 'provides',
    ent_col_head = 'name', ent_col_tail = 'all_hard_skills', ent_col_rel = None,
    c_head_func=exact_sim, c_tail_func=str_in_sim, c_rel_func = None)

  0%|          | 0/10180 [00:00<?, ?it/s]

In [ ]:
triples

[{'head': 'coursera_NJSdGN71Eeq4CApSN3OTvQ',
  'tail': 'hard_skills_7438',
  'rel': '_provides'},
 {'head': 'coursera_DMkcgX7LEeyRTg6FtAvfBw',
  'tail': 'hard_skills_7351',
  'rel': '_provides'},
 {'head': 'coursera_69Bku0KoEeWZtA4u62x6lQ',
  'tail': 'hard_skills_7573',
  'rel': '_provides'},
 {'head': 'coursera_0HiU7Oe4EeWTAQ4yevf_oQ',
  'tail': 'hard_skills_7431',
  'rel': '_provides'},
 {'head': 'coursera_sI_-QEBiEemtDRLx7Ne8jg',
  'tail': 'hard_skills_7282',
  'rel': '_provides'},
 {'head': 'coursera_2WtDgaCrEeyFDhLpwtOZqw',
  'tail': 'hard_skills_7190',
  'rel': '_provides'},
 {'head': 'coursera_rrZX06kxEeyjPxJkzIUqCw',
  'tail': 'hard_skills_7771',
  'rel': '_provides'},
 {'head': 'coursera_WFanvtoSEeedbRLwgi9a7A',
  'tail': 'hard_skills_7340',
  'rel': '_provides'},
 {'head': 'coursera_zjIfbv3pEeqRMRJTGi3b6Q',
  'tail': 'hard_skills_7915',
  'rel': '_provides'},
 {'head': 'coursera_k-WxP98PEeypqArgW5gGjw',
  'tail': 'hard_skills_7432',
  'rel': '_provides'},
 {'head': 'coursera_

In [ ]:
trips = get_all_triples()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: DtypeWarning: Columns (19,20) have mixed types.Specify dtype option on import or set low_memory=False.
  """Entry point for launching an IPython kernel.


  0%|          | 0/10180 [00:00<?, ?it/s]

  0%|          | 0/10180 [00:00<?, ?it/s]

In [ ]:
pd.DataFrame(trips)

head                             tail  \
0      coursera_NJSdGN71Eeq4CApSN3OTvQ                 hard_skills_7438   
1      coursera_DMkcgX7LEeyRTg6FtAvfBw                 hard_skills_7351   
2      coursera_69Bku0KoEeWZtA4u62x6lQ                 hard_skills_7573   
3      coursera_0HiU7Oe4EeWTAQ4yevf_oQ                 hard_skills_7431   
4      coursera_sI_-QEBiEemtDRLx7Ne8jg                 hard_skills_7282   
...                                ...                              ...   
15283                 hard_skills_8457  coursera_lf2q-R6UEeSzvSIAC0KYCQ   
15284                 hard_skills_7706  coursera_XSLeWQ6pEeu9ZBLzQTJEhw   
15285                 hard_skills_7771  coursera_7ErrkakwEeyxDg4ukgkVlw   
15286                 hard_skills_7417  coursera_xcqAU7oaEeq1DQ4cuiU-Sw   
15287                 hard_skills_7812  coursera_tJApe-HgEeeSKxKWkG_JMg   

               rel  
0        _provides  
1        _provides  
2        _provides  
3        _provides  
4        _provides  
...            ...  
15283  _aquired_by  
15284  _aquired_by  
15285  _aquired_by  
15286  _aquired_by  
15287  _aquired_by  

[15288 rows x 3 columns]

## Tests

In [ ]:
def great_nx_graph(df_, source_col, target_col, edge_col, edge_col_exist = False):
    # G = nx.Graph()
    df_['source'] = df_[source_col]
    df_['target'] = df_[target_col]
    if edge_col not in list(df_.columns):
        df_['edge_key'] = edge_col
    else:
        df_['edge_key'] = df_[edge_col]
    G = nx.from_pandas_edgelist(df_, edge_key = 'edge_key', edge_attr=True, create_using=nx.MultiGraph())
    # del df_[list(set(list(df_.columns)).difference(set(['source', 'target', 'edge_key'])))]
    return G
# def get_triple_entities(df_, head_ent, head_col, rel_col, tail_ent, tail_col):
#     # for h,r ,t in df_[head_col]
#     head_ent_data = 
#     tail_ent_data = 
#     for head_ent
#     pass

In [ ]:
def translate_df_to_rdf(graph, customer_data, customer_mapping):
    # Counter variable representing current row in the table
    i = 0
    num_rows = len(customer_data.index)

    # For each row in the table
    while i < num_rows:
        # Create URI subject for triples in this row using ‘Name’ column
        name = customer_data.loc[i, customer_mapping["uri"]]
        row_uri = create_eg_uri(name)

        # For each column/predicate mapping in mapping dictionary
        for column_name, predicate in customer_mapping.items():

            # Grab the value at this specific row/column entry
            value = customer_data.loc[i, column_name]

            # Strip extra characters from value
            if isinstance(value, str):
                value = value.strip()

            # Check if the value exists
            if not pd.isnull((value)):
                # Determine if object should be a URI or Literal
                if column_name in uri_objects:
                    # Create URI object and add triple to graph
                    uri_value = create_eg_uri(value)
                    graph.add((row_uri, predicate, uri_value))
                else:
                    # Create Literal object and add triple to graph
                    graph.add((row_uri, predicate, Literal(value)))
        i = i + 1

In [ ]:
graph = Graph()


In [ ]:
G = great_nx_graph(df_jobs, source_col='job_title', target_col = 'soft_skills', edge_col = 'has_skill', edge_col_exist = False)

In [ ]:
G.edges.data(keys=True)

In [ ]:
G = nx.Graph()

In [ ]:
G = nx.from_pandas_edgelist(df_jobs, source = 'job_title', target = 'soft_skills', edge_key = 'has_soft_skill')

In [ ]:
G['Chargés de Clientèle en Assistance Technique']

AtlasView({nan: {}, "Flexibilité|Distance émotionnelle|Extraversion|Besoin d'autonomie|Besoin de réflexion|Ambition|Implication au travail": {}, 'Flexibilité|Distance émotionnelle|Extraversion|Volonté de persuasion|Intuition / Spontanéité|Ambition': {}, "Flexibilité|Distance émotionnelle|Extraversion|Besoin d'autonomie|Ambition|Implication au travail|Besoin de réflexion": {}, 'Flexibilité|Distance émotionnelle|Extraversion|Conventionnel': {}, "Besoin d'autonomie|Besoin de réflexion|Ambition|Implication au travail|Flexibilité|Distance émotionnelle|Extraversion": {}, "Besoin d'autonomie|Besoin de réflexion|Ambition|Implication au travail|Recherche de nouveauté": {}, "Extraversion|Distance émotionnelle|Flexibilité|Besoin d'autonomie|Besoin de réflexion|Ambition|Implication au travail": {}, 'Conventionnel|Extraversion|Distance émotionnelle|Flexibilité': {}})

In [ ]:
G.edges.data(keys = True)

TypeError: ignored

EdgeView([('Chargés de Clientèle en Assistance Technique', nan), ('Chargés de Clientèle en Assistance Technique', "Flexibilité|Distance émotionnelle|Extraversion|Besoin d'autonomie|Besoin de réflexion|Ambition|Implication au travail"), ('Chargés de Clientèle en Assistance Technique', 'Flexibilité|Distance émotionnelle|Extraversion|Volonté de persuasion|Intuition / Spontanéité|Ambition'), ('Chargés de Clientèle en Assistance Technique', "Flexibilité|Distance émotionnelle|Extraversion|Besoin d'autonomie|Ambition|Implication au travail|Besoin de réflexion"), ('Chargés de Clientèle en Assistance Technique', 'Flexibilité|Distance émotionnelle|Extraversion|Conventionnel'), ('Chargés de Clientèle en Assistance Technique', "Besoin d'autonomie|Besoin de réflexion|Ambition|Implication au travail|Flexibilité|Distance émotionnelle|Extraversion"), ('Chargés de Clientèle en Assistance Technique', "Besoin d'autonomie|Besoin de réflexion|Ambition|Implication au travail|Recherche de nouveauté"), ('Char

In [ ]:
G.nodes()

NodeView(('Chargés de Clientèle en Assistance Technique', nan, 'Consultant Junior', 'Flexibilité|Organisation|Rationalisme|Besoin de réflexion', 'Directeur Administratif et Financier', "Flexibilité|Extraversion|Organisation|Rationalisme|Implication au travail|Besoin d'objectivité|Respect des règles|Conventionnel", 'Sales Managers Hispanophones', 'Volonté de persuasion|Extraversion|Intuition / Spontanéité|Ambition|Flexibilité|Distance émotionnelle', 'Sales Managers Francophones', 'Flexibilité|Extraversion|Organisation|Rationalisme|Implication au travail|Distance émotionnelle|Conventionnel', 'Technical Support Managers', 'Flexibilité|Extraversion|Organisation|Rationalisme|Implication au travail', 'Project Manager (anglais courant)', 'Quality Process Manager (anglais courant)', "Besoin d'objectivité|Ténacité|Organisation|Rationalisme|Respect des règles", 'Responsable Ressources Humaines', "Besoin d'objectivité|Extraversion|Besoin d'autonomie|Implication au travail|Recherche de nouveauté",

In [ ]:
G = nx.from_pandas_edgelist(df_jobs, source = 'job_title', target = 'soft_skills', edge_key = 'has_soft_skill')

In [ ]:
figure(figsize=(10, 8))
nx.draw_shell(G, with_labels=True)

/usr/local/lib/python3.7/dist-packages/matplotlib/backends/backend_agg.py:214: RuntimeWarning: Glyph 9 missing from current font.
  font.set_text(s, 0.0, flags=flags)
/usr/local/lib/python3.7/dist-packages/matplotlib/backends/backend_agg.py:183: RuntimeWarning: Glyph 9 missing from current font.
  font.set_text(s, 0, flags=flags)


Error in callback <function flush_figures at 0x7f95ed62c200> (for post_execute):


KeyboardInterrupt: ignored

In [ ]:
customer_mapping = {
    "uri": "Customer Name",
    "Customer ID": create_eg_uri("customerId"),
    "Customer Name": create_eg_uri("customerName"),
    "Owns Product": create_eg_uri("owns"),
}

product_mapping = {

    "uri": "Product Name",
    "Product ID": create_eg_uri("productId"),
    "Product Name": create_eg_uri("productName"),
    "Composed of": create_eg_uri("isComposedOf"),
}

part_mapping = {

    "uri": "Part Name",
    "Part ID": create_eg_uri("partId"),
    "Part Name": create_eg_uri("partName"),
    "Action": create_eg_uri("needs"),
}

uri_objects = ["Owns Product", "Composed of", "Action"]